In [ ]:
# 安装 torch torchaudio torchvision
!pip install torch==2.0.0+cu118 torchaudio==2.0.1+cu118 torchvision==0.15.1+cu118 --index-url https://download.pytorch.org/whl/cu118

development

In [1]:
import torch
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:  
 print('Not connected to a GPU')
else:  
 print(gpu_info)
use_cuda = torch.cuda.is_available()

Sat Jan 31 14:47:48 2026       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 576.40                 Driver Version: 576.40         CUDA Version: 12.9     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                  Driver-Model | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA GeForce RTX 3090      WDDM  |   00000000:01:00.0  On |                  N/A |
|  0%   39C    P8             27W /  390W |   14582MiB /  24576MiB |      7%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [2]:
SEED = 42
WEIGHTED = True

In [3]:
from datasets import *
import pandas as pd
import numpy as np
train = pd.DataFrame(load_dataset("dev_phase2/subtask3/train/eng", split="train"))
val = pd.DataFrame(load_dataset("dev_phase2/subtask3/train/eng", split="train"))
test = pd.DataFrame(load_dataset("dev_phase2/subtask3/dev/eng", split="train"))
test_final = pd.DataFrame(load_dataset("test_phase/subtask3/test/eng", split="train"))
train.head()

C:\Users\8888\Anaconda3\envs\SemEval2025_Task11\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Generating train split: 1452 examples [00:00, 136703.24 examples/s]


id  \
0  eng_973938b90b0ff5d87d35a582f83f5c89   
1  eng_07dfd4600426caca6e2c5883fcbea9ea   
2  eng_f14519ff2302b6cd47712073f13bc461   
3  eng_e48b7e7542faafa544ac57b64bc80daf   
4  eng_7c581fb77bce8033aeba3d6dbd6273eb   

                                                text  stereotype  \
0           is defending imperialism in the dnd chat           0   
1  Still playing with this. I am now following Ra...           0   
2  .senate.gov Theres 3 groups out there Republic...           0   
3  "ABC MD, David Anderson, said the additional f...           0   
4  "bad people" I have some conservative values s...           0   

   vilification  dehumanization  extreme_language  lack_of_empathy  \
0             0               0                 0                0   
1             0               0                 0                0   
2             0               0                 0                0   
3             0               0                 0                0   
4             0               0                 0                0   

   invalidation  
0             0  
1             0  
2             0  
3             0  
4             0

In [4]:
labels = ["stereotype", "vilification", "dehumanization", "extreme_language", "lack_of_empathy", "invalidation"]
def get_text_and_label(df):  
  return df.rename(columns={"text": "text"})[["text"] + labels]
train = get_text_and_label(train)
print(f"Dataset size: <{len(train.index)}:{len(val.index)}:{len(test.index)}:{len(test_final.index)}>")
train.head(10)

Dataset size: <2676:2676:133:1452>


text  stereotype  \
0           is defending imperialism in the dnd chat           0   
1  Still playing with this. I am now following Ra...           0   
2  .senate.gov Theres 3 groups out there Republic...           0   
3  "ABC MD, David Anderson, said the additional f...           0   
4  "bad people" I have some conservative values s...           0   
5  "Enemy of the people" was a phrase coined and ...           0   
6  "He also voiced support for Elon Musk, Tommy R...           0   
7  "If you disagree with imperialism, youre a sup...           0   
8  "italian" as a national identity is totally ov...           0   
9    "No to ethnic cleansing". QudsDay QudsMainIssue           0   

   vilification  dehumanization  extreme_language  lack_of_empathy  \
0             0               0                 0                0   
1             0               0                 0                0   
2             0               0                 0                0   
3             0               0                 0                0   
4             0               0                 0                0   
5             0               0                 0                0   
6             0               0                 0                0   
7             0               0                 0                0   
8             0               0                 0                0   
9             0               0                 0                0   

   invalidation  
0             0  
1             0  
2             0  
3             0  
4             0  
5             0  
6             0  
7             0  
8             0  
9             0

In [5]:
val = get_text_and_label(val)
val.head(10)

text  stereotype  \
0           is defending imperialism in the dnd chat           0   
1  Still playing with this. I am now following Ra...           0   
2  .senate.gov Theres 3 groups out there Republic...           0   
3  "ABC MD, David Anderson, said the additional f...           0   
4  "bad people" I have some conservative values s...           0   
5  "Enemy of the people" was a phrase coined and ...           0   
6  "He also voiced support for Elon Musk, Tommy R...           0   
7  "If you disagree with imperialism, youre a sup...           0   
8  "italian" as a national identity is totally ov...           0   
9    "No to ethnic cleansing". QudsDay QudsMainIssue           0   

   vilification  dehumanization  extreme_language  lack_of_empathy  \
0             0               0                 0                0   
1             0               0                 0                0   
2             0               0                 0                0   
3             0               0                 0                0   
4             0               0                 0                0   
5             0               0                 0                0   
6             0               0                 0                0   
7             0               0                 0                0   
8             0               0                 0                0   
9             0               0                 0                0   

   invalidation  
0             0  
1             0  
2             0  
3             0  
4             0  
5             0  
6             0  
7             0  
8             0  
9             0

In [6]:
test = get_text_and_label(test)
test.head(10)

text stereotype vilification  \
0                   God is with Ukraine and Zelensky       None         None   
1  4 Dems, 2 Republicans Luzerne County Council s...       None         None   
2  Abuse Survivor Recounts Her Struggles at YWCA ...       None         None   
3    After Rwanda, another deportation camp disaster       None         None   
4  Another plea in Trump election interference probe       None         None   
5              any number of southern red states tbh       None         None   
6     Breitbart is the new age grocery aisle tabloid       None         None   
7     Congressman talks border security, debit limit       None         None   
8  Cooke Co. GOP incumbents announce reelection runs       None         None   
9                 Could one overwhelm the iron dome?       None         None   

  dehumanization extreme_language lack_of_empathy invalidation  
0           None             None            None         None  
1           None             None            None         None  
2           None             None            None         None  
3           None             None            None         None  
4           None             None            None         None  
5           None             None            None         None  
6           None             None            None         None  
7           None             None            None         None  
8           None             None            None         None  
9           None             None            None         None

In [7]:
test_final = get_text_and_label(test_final)
test_final.head(10)

text stereotype vilification  \
0  OP! Podcast where you ascertain the immigratio...       None         None   
1  "...the latest sign that Israel is planning fo...       None         None   
2  "Ice discs, ice circles, ice pans, ice pancake...       None         None   
3  "Since 2021, USAIDWest Bank and Gaza has inves...       None         None   
4  "The Cybersecurity Infrastructure Security Age...       None         None   
5  "What is lacking about your identity?" Nothing...       None         None   
6  1 x.comImamofpeace... Four key facts Hezbollah...       None         None   
7   11 more hostages freed in Gaza IsraelHamas truce       None         None   
8  2024 Republican race is a referendum on Joe Bi...       None         None   
9            2026 impeachment is coming. Maybe 2025.       None         None   

  dehumanization extreme_language lack_of_empathy invalidation  
0           None             None            None         None  
1           None             None            None         None  
2           None             None            None         None  
3           None             None            None         None  
4           None             None            None         None  
5           None             None            None         None  
6           None             None            None         None  
7           None             None            None         None  
8           None             None            None         None  
9           None             None            None         None

In [8]:
def generate_multilabel_df(df):
  df["labels"] = np.empty((len(df), len(labels))).tolist()
  for index, row in df.iterrows():
    row_labels = [row[label] for label in labels]
    for i in range(len(labels)):
      df.loc[index, "labels"][i] = row_labels[i]
  return df[["text", "labels"]]
train = generate_multilabel_df(train)
val = generate_multilabel_df(val)
test = generate_multilabel_df(test)
test_final = generate_multilabel_df(test_final)
train.head(10)

text              labels
0           is defending imperialism in the dnd chat  [0, 0, 0, 0, 0, 0]
1  Still playing with this. I am now following Ra...  [0, 0, 0, 0, 0, 0]
2  .senate.gov Theres 3 groups out there Republic...  [0, 0, 0, 0, 0, 0]
3  "ABC MD, David Anderson, said the additional f...  [0, 0, 0, 0, 0, 0]
4  "bad people" I have some conservative values s...  [0, 0, 0, 0, 0, 0]
5  "Enemy of the people" was a phrase coined and ...  [0, 0, 0, 0, 0, 0]
6  "He also voiced support for Elon Musk, Tommy R...  [0, 0, 0, 0, 0, 0]
7  "If you disagree with imperialism, youre a sup...  [0, 0, 0, 0, 0, 0]
8  "italian" as a national identity is totally ov...  [0, 0, 0, 0, 0, 0]
9    "No to ethnic cleansing". QudsDay QudsMainIssue  [0, 0, 0, 0, 0, 0]

In [9]:
test.head(10)

text  \
0                   God is with Ukraine and Zelensky   
1  4 Dems, 2 Republicans Luzerne County Council s...   
2  Abuse Survivor Recounts Her Struggles at YWCA ...   
3    After Rwanda, another deportation camp disaster   
4  Another plea in Trump election interference probe   
5              any number of southern red states tbh   
6     Breitbart is the new age grocery aisle tabloid   
7     Congressman talks border security, debit limit   
8  Cooke Co. GOP incumbents announce reelection runs   
9                 Could one overwhelm the iron dome?   

                                 labels  
0  [None, None, None, None, None, None]  
1  [None, None, None, None, None, None]  
2  [None, None, None, None, None, None]  
3  [None, None, None, None, None, None]  
4  [None, None, None, None, None, None]  
5  [None, None, None, None, None, None]  
6  [None, None, None, None, None, None]  
7  [None, None, None, None, None, None]  
8  [None, None, None, None, None, None]  
9  [None, None, None, None, None, None]

In [10]:
test_final.head(10)

text  \
0  OP! Podcast where you ascertain the immigratio...   
1  "...the latest sign that Israel is planning fo...   
2  "Ice discs, ice circles, ice pans, ice pancake...   
3  "Since 2021, USAIDWest Bank and Gaza has inves...   
4  "The Cybersecurity Infrastructure Security Age...   
5  "What is lacking about your identity?" Nothing...   
6  1 x.comImamofpeace... Four key facts Hezbollah...   
7   11 more hostages freed in Gaza IsraelHamas truce   
8  2024 Republican race is a referendum on Joe Bi...   
9            2026 impeachment is coming. Maybe 2025.   

                                 labels  
0  [None, None, None, None, None, None]  
1  [None, None, None, None, None, None]  
2  [None, None, None, None, None, None]  
3  [None, None, None, None, None, None]  
4  [None, None, None, None, None, None]  
5  [None, None, None, None, None, None]  
6  [None, None, None, None, None, None]  
7  [None, None, None, None, None, None]  
8  [None, None, None, None, None, None]  
9  [None, None, None, None, None, None]

In [11]:
from datetime import datetime, timedelta
import os
PATH = "./outputs/{}/".format((datetime.now() + timedelta(hours=2)).strftime("%d-%m-%Y-%H-%M"))
print("Current working dir:", PATH)
os.mkdir(PATH)

Current working dir: ./outputs/31-01-2026-16-53/


In [12]:
models = {
    "mbert-cased": {
        "model_type": "bert",
        "model_name": "models--google-bert--bert-base-multilingual-cased"
    },
    "mbert-uncased": {
        "model_type": "bert",
        "model_name": "models--google-bert--bert-base-multilingual-uncased"
    },
    "roberta": {
        "model_type": "roberta",
        "model_name": "models--FacebookAI--roberta-base"
    },
    "beto-cased": {
        "model_type": "bert",
        "model_name": "models--dccuchile--bert-base-spanish-wwm-cased"
    },
    "beto-uncased": {
        "model_type": "bert",
        "model_name": "models--dccuchile--bert-base-spanish-wwm-uncased"
    },
    "distilbert-multi": {
        "model_type": "distilbert",
        "model_name": "models--distilbert--distilbert-base-multilingual-cased"
    }
}

In [13]:
from simpletransformers.classification import MultiLabelClassificationModel, MultiLabelClassificationArgs
for model, fields in models.items():
  model_args = MultiLabelClassificationArgs(
      overwrite_output_dir= True,
      eval_batch_size=8,
      num_train_epochs=5,
      learning_rate = 4e-05,
      optimizer="AdamW",
      manual_seed=SEED,
      use_early_stopping=True,
      save_model_every_epoch=False
  )
  model_args.output_dir = os.path.join(PATH, model)
  models[model] = MultiLabelClassificationModel(fields["model_type"], fields["model_name"],
                                      args=model_args, num_labels=len(labels), use_cuda=use_cuda)

Some weights of BertForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--google-bert--bert-base-multilingual-cased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of BertForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--google-bert--bert-base-multilingual-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of RobertaForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--FacebookAI--roberta-base and are newly initialized: ['classifier.out_proj.weight', 'classifier.dense.weight', 'roberta.pooler.dense.bias', 'roberta.pooler.dense.weight', 'classifier.dense.bias', 'classifier.out_

In [14]:
from sklearn.metrics import mean_squared_error
from math import sqrt
def root_mean_squared_error(y_true, y_pred):    
  return sqrt(mean_squared_error(y_true, y_pred))

In [ ]:
for model_name, model in models.items():
  model.train_model(train, loss_fct=root_mean_squared_error)

6it [00:04,  1.29it/s]                                                                                                                                                                                                                  
Epochs 5/5. Running Loss:    0.2572:  69%|████████████████████████████████████████████████████████████████████████████████████████████████████████████                                                | 232/335 [00:16<00:09, 11.37it/s]

Epoch 5 of 5: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 5/5 [01:42<00:00, 20.53s/it]
6it [00:05,  1.09it/s]                                                                                                                                                                                                                  
Epoch 5 of 5: 100%|████████████████████████████████████████████████

In [19]:
import collections
from itertools import combinations
models_names = list(models.keys())
ensembles_list = list()
for i in range(1, len(models_names) + 1):
    ensembles_list += list(combinations(models_names, i))
ensembles_list = [list(ensemble) for ensemble in ensembles_list]
ensembles = {}
for i in range(len(ensembles_list)):
  ensembles["ensemble{:02d}".format(i)] = {}
  ensembles["ensemble{:02d}".format(i)]["models"] = ensembles_list[i]
  ensembles["ensemble{:02d}".format(i)]["metrics"] = {}
ensembles

{'ensemble00': {'models': ['mbert-cased'], 'metrics': {}},
 'ensemble01': {'models': ['mbert-uncased'], 'metrics': {}},
 'ensemble02': {'models': ['roberta'], 'metrics': {}},
 'ensemble03': {'models': ['beto-cased'], 'metrics': {}},
 'ensemble04': {'models': ['beto-uncased'], 'metrics': {}},
 'ensemble05': {'models': ['distilbert-multi'], 'metrics': {}},
 'ensemble06': {'models': ['mbert-cased', 'mbert-uncased'], 'metrics': {}},
 'ensemble07': {'models': ['mbert-cased', 'roberta'], 'metrics': {}},
 'ensemble08': {'models': ['mbert-cased', 'beto-cased'], 'metrics': {}},
 'ensemble09': {'models': ['mbert-cased', 'beto-uncased'], 'metrics': {}},
 'ensemble10': {'models': ['mbert-cased', 'distilbert-multi'], 'metrics': {}},
 'ensemble11': {'models': ['mbert-uncased', 'roberta'], 'metrics': {}},
 'ensemble12': {'models': ['mbert-uncased', 'beto-cased'], 'metrics': {}},
 'ensemble13': {'models': ['mbert-uncased', 'beto-uncased'], 'metrics': {}},
 'ensemble14': {'models': ['mbert-uncased', 'd

In [20]:
from sklearn.metrics import accuracy_score, precision_recall_fscore_support, f1_score
def compute_metrics(y_true, y_pred):
  macro_precision, macro_recall, macro_f1, _ = precision_recall_fscore_support(y_true, y_pred, average='macro')
  acc = accuracy_score(y_true, y_pred)
  weighted_f1 = f1_score(y_true, y_pred, average='weighted')
  return {
      'accuracy': round(acc, 5),
      'macro_f1': round(macro_f1, 5),
      'macro_precision': round(macro_precision, 5),
      'macro_recall': round(macro_recall, 5),
      'weighted_f1': round(weighted_f1, 5)
  }
model_evaluation = {}
for model_name in models:
  model_evaluation[model_name] = {}
  result, model_outputs, wrong_predictions = models[model_name].eval_model(val, metric=root_mean_squared_error)
  model_evaluation[model_name]["result"] = result                                                                   
  model_evaluation[model_name]["val_model_outputs"] = model_outputs                                                 
  model_evaluation[model_name]["val_predictions"] = list ()
  for output in model_outputs:
    model_evaluation[model_name]["val_predictions"].append([0 if lab_output < 0.5 else 1 for lab_output in output]) 
  model_evaluation[model_name]["val_wrong_predictions"] = wrong_predictions                                         
  model_evaluation[model_name]["metrics"] = compute_metrics(val.get("labels").tolist(), model_evaluation[model_name].get("val_predictions"))
  print(f"{model_name}\t", model_evaluation[model_name].get("metrics"))

6it [00:04,  1.21it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 335/335 [00:04<00:00, 74.73it/s]


mbert-cased	 {'accuracy': 0.69021, 'macro_f1': 0.71216, 'macro_precision': 0.7351, 'macro_recall': 0.71267, 'weighted_f1': 0.74921}


6it [00:04,  1.34it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 335/335 [00:04<00:00, 78.16it/s]


mbert-uncased	 {'accuracy': 0.69432, 'macro_f1': 0.74711, 'macro_precision': 0.75184, 'macro_recall': 0.75178, 'weighted_f1': 0.77145}


6it [00:04,  1.43it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 335/335 [00:04<00:00, 74.86it/s]


...

beto-cased	 {'accuracy': 0.6861, 'macro_f1': 0.73743, 'macro_precision': 0.7218, 'macro_recall': 0.76175, 'weighted_f1': 0.76394}


6it [00:04,  1.44it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 335/335 [00:04<00:00, 75.88it/s]


beto-uncased	 {'accuracy': 0.6775, 'macro_f1': 0.71638, 'macro_precision': 0.71496, 'macro_recall': 0.72691, 'weighted_f1': 0.7472}


6it [00:04,  1.40it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 335/335 [00:02<00:00, 129.02it/s]


distilbert-multi	 {'accuracy': 0.71338, 'macro_f1': 0.76419, 'macro_precision': 0.77634, 'macro_recall': 0.76061, 'weighted_f1': 0.7864}


In [21]:
from sklearn.preprocessing import normalize
def vote(predictions, weighted=False, weights=None):
  votes = list()  
  for i in range(len(labels)):    
    curr_label_preds = [preds[i] for preds in predictions]    
    voting = sum(curr_label_preds * weights) if weighted else sum(curr_label_preds)/len(curr_label_preds)
    votes.append(0 if voting < 0.5 else 1)  
  return votes
ensemble_evaluation = {}
def predict_ensemble(ensemble_name, dataset_name, dataset, weighted=False):
  ensemble_evaluation[ensemble_name][f"{dataset_name}_predictions"] = list()  
  for i in range(len(dataset.index)):
    predictions = list()
    ensemble_models = ensembles[ensemble_name].get("models")      
    for model_name in ensemble_models:
      curr_model_outputs = model_evaluation[model_name].get(f"{dataset_name}_model_outputs")
      predictions.append(curr_model_outputs[i])
    weights = list()    
    if weighted:      
      f1_scores_list = [model_evaluation[model_name]["metrics"].get("weighted_f1")                        
                        for model_name in ensembles[ensemble_name].get("models")]
      weights = normalize([f1_scores_list], norm="l1")[0]
    ensemble_pred = vote(predictions, weighted, weights)
    ensemble_evaluation[ensemble_name][f"{dataset_name}_predictions"].append(ensemble_pred)
for ensemble_name in ensembles:
  ensemble_evaluation[ensemble_name] = {}
  ensemble_evaluation[ensemble_name]["val_predictions"] = list()
  predict_ensemble(ensemble_name, "val", val, weighted=WEIGHTED)
  ensembles[ensemble_name]["metrics"] = compute_metrics(val.get("labels").tolist(), ensemble_evaluation[ensemble_name].get("val_predictions"))  
  print(f"{ensemble_name}\t", ensembles[ensemble_name].get("metrics"))

ensemble00	 {'accuracy': 0.69021, 'macro_f1': 0.71216, 'macro_precision': 0.7351, 'macro_recall': 0.71267, 'weighted_f1': 0.74921}
ensemble01	 {'accuracy': 0.69432, 'macro_f1': 0.74711, 'macro_precision': 0.75184, 'macro_recall': 0.75178, 'weighted_f1': 0.77145}
ensemble02	 {'accuracy': 0.66928, 'macro_f1': 0.66934, 'macro_precision': 0.73309, 'macro_recall': 0.65757, 'weighted_f1': 0.71043}
ensemble03	 {'accuracy': 0.6861, 'macro_f1': 0.73743, 'macro_precision': 0.7218, 'macro_recall': 0.76175, 'weighted_f1': 0.76394}
ensemble04	 {'accuracy': 0.6775, 'macro_f1': 0.71638, 'macro_precision': 0.71496, 'macro_recall': 0.72691, 'weighted_f1': 0.7472}
ensemble05	 {'accuracy': 0.71338, 'macro_f1': 0.76419, 'macro_precision': 0.77634, 'macro_recall': 0.76061, 'weighted_f1': 0.7864}
ensemble06	 {'accuracy': 0.70291, 'macro_f1': 0.75007, 'macro_precision': 0.77555, 'macro_recall': 0.743, 'weighted_f1': 0.77843}
ensemble07	 {'accuracy': 0.68834, 'macro_f1': 0.69881, 'macro_precision': 0.75972, '

In [22]:
import json
with open(os.path.join(PATH, 'ensembles.json'), 'w', encoding='utf-8') as f:
    json.dump(ensembles, f, ensure_ascii=False, indent=4)

In [23]:
f1_scores = {ensemble_name: ensembles[ensemble_name]["metrics"].get("weighted_f1") for ensemble_name in ensemble_evaluation}
best_ensemble_name = max(f1_scores, key=f1_scores.get)
best_ensemble = {"name": best_ensemble_name,                 
                "models": ensembles[best_ensemble_name].get("models"),                 
                "metrics": ensembles[best_ensemble_name].get("metrics")                 
                }
best_ensemble

{'name': 'ensemble35',
 'models': ['mbert-uncased', 'beto-cased', 'distilbert-multi'],
 'metrics': {'accuracy': 0.71487,
  'macro_f1': 0.77314,
  'macro_precision': 0.79133,
  'macro_recall': 0.76796,
  'weighted_f1': 0.79643}}

In [24]:
for model_name in models:
  model_predictions, model_raw_outputs = models.get(model_name).predict(test["text"].tolist())
  model_evaluation[model_name]["test_model_outputs"] = model_raw_outputs
  model_evaluation[model_name]["test_predictions"] = list ()  
  for output in model_raw_outputs:
    model_evaluation[model_name]["test_predictions"].append([0 if lab_output < 0.5 else 1 for lab_output in output])
predict_ensemble(best_ensemble.get("name"), "test", test, weighted=WEIGHTED)

1it [00:03,  3.31s/it]
100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 17/17 [00:00<00:00, 40.90it/s]
1it [00:03,  3.23s/it]
100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 17/17 [00:00<00:00, 37.07it/s]
1it [00:03,  3.26s/it]
100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 17/17 [00:00<00:00, 33.03it/s]
1it [00:03,  3.26s/it]
100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 17/17 [

In [25]:
for model_name, evaluation in model_evaluation.items():
  curr_model = model_evaluation.get(model_name)
  curr_model["val_model_outputs"] = [list(output) for output in curr_model.get("val_model_outputs")]
  curr_model["test_model_outputs"] = [list(output) for output in curr_model.get("test_model_outputs")]
  curr_model["val_predictions"] = list(curr_model.get("val_predictions"))
  curr_model["test_predictions"] = list(curr_model.get("test_predictions"))
  if curr_model.get("val_wrong_predictions"):
    curr_model["val_wrong_predictions_list"] = curr_model.get("val_wrong_predictions")
    curr_model["val_wrong_predictions"] = {}
    for pred in curr_model.get("val_wrong_predictions_list"):
      curr_model["val_wrong_predictions"][pred.guid] = {
          "text_a": pred.text_a,
          "text_b": pred.text_b,
          "label": pred.label
      }
    del curr_model["val_wrong_predictions_list"]

  with open(os.path.join(PATH, f'{model_name}/model-evaluation.json'), 'w', encoding='utf-8') as f:
    json.dump(curr_model, f, ensure_ascii=False, indent=4)

In [26]:
best_ensemble["val_predictions"] = ensemble_evaluation[best_ensemble.get("name")].get("val_predictions")
best_ensemble["test_predictions"] = ensemble_evaluation[best_ensemble.get("name")].get("test_predictions")
with open(os.path.join(PATH, 'best-ensemble.json'), 'w', encoding='utf-8') as f:
    json.dump(best_ensemble, f, ensure_ascii=False, indent=4)

In [27]:
test["predicted_labels"] = ensemble_evaluation[best_ensemble.get("name")].get("test_predictions")
test.head(10)

text  \
0                   God is with Ukraine and Zelensky   
1  4 Dems, 2 Republicans Luzerne County Council s...   
2  Abuse Survivor Recounts Her Struggles at YWCA ...   
3    After Rwanda, another deportation camp disaster   
4  Another plea in Trump election interference probe   
5              any number of southern red states tbh   
6     Breitbart is the new age grocery aisle tabloid   
7     Congressman talks border security, debit limit   
8  Cooke Co. GOP incumbents announce reelection runs   
9                 Could one overwhelm the iron dome?   

                                 labels    predicted_labels  
0  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
1  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
2  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
3  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
4  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
5  [None, None, None, None, None, None]  [0, 1, 0, 0, 0, 0]  
6  [None, None, None, None, None, None]  [0, 1, 0, 0, 0, 0]  
7  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
8  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
9  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]

In [28]:
test.to_csv(os.path.join(PATH, "test-predictions.csv"), index=False)  

test

In [29]:
import torch
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:  
 print('Not connected to a GPU')
else:  
 print(gpu_info)
use_cuda = torch.cuda.is_available()

Sat Jan 31 16:16:43 2026       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 576.40                 Driver Version: 576.40         CUDA Version: 12.9     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                  Driver-Model | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA GeForce RTX 3090      WDDM  |   00000000:01:00.0  On |                  N/A |
|  0%   38C    P8             27W /  390W |   21156MiB /  24576MiB |     14%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [30]:
SEED = 42
WEIGHTED = True

In [31]:
from datasets import *
import pandas as pd
import numpy as np
train = pd.DataFrame(load_dataset("dev_phase2/subtask3/train/eng", split="train"))
val = pd.DataFrame(load_dataset("dev_phase2/subtask3/train/eng", split="train"))
test = pd.DataFrame(load_dataset("dev_phase2/subtask3/dev/eng", split="train"))
test_final = pd.DataFrame(load_dataset("test_phase/subtask3/test/eng", split="train"))
train.head()

id  \
0  eng_973938b90b0ff5d87d35a582f83f5c89   
1  eng_07dfd4600426caca6e2c5883fcbea9ea   
2  eng_f14519ff2302b6cd47712073f13bc461   
3  eng_e48b7e7542faafa544ac57b64bc80daf   
4  eng_7c581fb77bce8033aeba3d6dbd6273eb   

                                                text  stereotype  \
0           is defending imperialism in the dnd chat           0   
1  Still playing with this. I am now following Ra...           0   
2  .senate.gov Theres 3 groups out there Republic...           0   
3  "ABC MD, David Anderson, said the additional f...           0   
4  "bad people" I have some conservative values s...           0   

   vilification  dehumanization  extreme_language  lack_of_empathy  \
0             0               0                 0                0   
1             0               0                 0                0   
2             0               0                 0                0   
3             0               0                 0                0   
4             0               0                 0                0   

   invalidation  
0             0  
1             0  
2             0  
3             0  
4             0

In [32]:
labels = ["stereotype", "vilification", "dehumanization", "extreme_language", "lack_of_empathy", "invalidation"]
def get_text_and_label(df):  
  return df.rename(columns={"text": "text"})[["text"] + labels]
train = get_text_and_label(train)
print(f"Dataset size: <{len(train.index)}:{len(val.index)}:{len(test.index)}:{len(test_final.index)}>")
train.head(10)

Dataset size: <2676:2676:133:1452>


text  stereotype  \
0           is defending imperialism in the dnd chat           0   
1  Still playing with this. I am now following Ra...           0   
2  .senate.gov Theres 3 groups out there Republic...           0   
3  "ABC MD, David Anderson, said the additional f...           0   
4  "bad people" I have some conservative values s...           0   
5  "Enemy of the people" was a phrase coined and ...           0   
6  "He also voiced support for Elon Musk, Tommy R...           0   
7  "If you disagree with imperialism, youre a sup...           0   
8  "italian" as a national identity is totally ov...           0   
9    "No to ethnic cleansing". QudsDay QudsMainIssue           0   

   vilification  dehumanization  extreme_language  lack_of_empathy  \
0             0               0                 0                0   
1             0               0                 0                0   
2             0               0                 0                0   
3             0               0                 0                0   
4             0               0                 0                0   
5             0               0                 0                0   
6             0               0                 0                0   
7             0               0                 0                0   
8             0               0                 0                0   
9             0               0                 0                0   

   invalidation  
0             0  
1             0  
2             0  
3             0  
4             0  
5             0  
6             0  
7             0  
8             0  
9             0

In [33]:
val = get_text_and_label(val)
val.head(10)

text  stereotype  \
0           is defending imperialism in the dnd chat           0   
1  Still playing with this. I am now following Ra...           0   
2  .senate.gov Theres 3 groups out there Republic...           0   
3  "ABC MD, David Anderson, said the additional f...           0   
4  "bad people" I have some conservative values s...           0   
5  "Enemy of the people" was a phrase coined and ...           0   
6  "He also voiced support for Elon Musk, Tommy R...           0   
7  "If you disagree with imperialism, youre a sup...           0   
8  "italian" as a national identity is totally ov...           0   
9    "No to ethnic cleansing". QudsDay QudsMainIssue           0   

   vilification  dehumanization  extreme_language  lack_of_empathy  \
0             0               0                 0                0   
1             0               0                 0                0   
2             0               0                 0                0   
3             0               0                 0                0   
4             0               0                 0                0   
5             0               0                 0                0   
6             0               0                 0                0   
7             0               0                 0                0   
8             0               0                 0                0   
9             0               0                 0                0   

   invalidation  
0             0  
1             0  
2             0  
3             0  
4             0  
5             0  
6             0  
7             0  
8             0  
9             0

In [34]:
test = get_text_and_label(test)
test.head(10)

text stereotype vilification  \
0                   God is with Ukraine and Zelensky       None         None   
1  4 Dems, 2 Republicans Luzerne County Council s...       None         None   
2  Abuse Survivor Recounts Her Struggles at YWCA ...       None         None   
3    After Rwanda, another deportation camp disaster       None         None   
4  Another plea in Trump election interference probe       None         None   
5              any number of southern red states tbh       None         None   
6     Breitbart is the new age grocery aisle tabloid       None         None   
7     Congressman talks border security, debit limit       None         None   
8  Cooke Co. GOP incumbents announce reelection runs       None         None   
9                 Could one overwhelm the iron dome?       None         None   

  dehumanization extreme_language lack_of_empathy invalidation  
0           None             None            None         None  
1           None             None            None         None  
2           None             None            None         None  
3           None             None            None         None  
4           None             None            None         None  
5           None             None            None         None  
6           None             None            None         None  
7           None             None            None         None  
8           None             None            None         None  
9           None             None            None         None

In [35]:
test_final = get_text_and_label(test_final)
test_final.head(10)

text stereotype vilification  \
0  OP! Podcast where you ascertain the immigratio...       None         None   
1  "...the latest sign that Israel is planning fo...       None         None   
2  "Ice discs, ice circles, ice pans, ice pancake...       None         None   
3  "Since 2021, USAIDWest Bank and Gaza has inves...       None         None   
4  "The Cybersecurity Infrastructure Security Age...       None         None   
5  "What is lacking about your identity?" Nothing...       None         None   
6  1 x.comImamofpeace... Four key facts Hezbollah...       None         None   
7   11 more hostages freed in Gaza IsraelHamas truce       None         None   
8  2024 Republican race is a referendum on Joe Bi...       None         None   
9            2026 impeachment is coming. Maybe 2025.       None         None   

  dehumanization extreme_language lack_of_empathy invalidation  
0           None             None            None         None  
1           None             None            None         None  
2           None             None            None         None  
3           None             None            None         None  
4           None             None            None         None  
5           None             None            None         None  
6           None             None            None         None  
7           None             None            None         None  
8           None             None            None         None  
9           None             None            None         None

In [36]:
def generate_multilabel_df(df):
  df["labels"] = np.empty((len(df), len(labels))).tolist()
  for index, row in df.iterrows():
    row_labels = [row[label] for label in labels]
    for i in range(len(labels)):
      df.loc[index, "labels"][i] = row_labels[i]
  return df[["text", "labels"]]
train = generate_multilabel_df(train)
val = generate_multilabel_df(val)
test = generate_multilabel_df(test)
test_final = generate_multilabel_df(test_final)
train.head(10)

text              labels
0           is defending imperialism in the dnd chat  [0, 0, 0, 0, 0, 0]
1  Still playing with this. I am now following Ra...  [0, 0, 0, 0, 0, 0]
2  .senate.gov Theres 3 groups out there Republic...  [0, 0, 0, 0, 0, 0]
3  "ABC MD, David Anderson, said the additional f...  [0, 0, 0, 0, 0, 0]
4  "bad people" I have some conservative values s...  [0, 0, 0, 0, 0, 0]
5  "Enemy of the people" was a phrase coined and ...  [0, 0, 0, 0, 0, 0]
6  "He also voiced support for Elon Musk, Tommy R...  [0, 0, 0, 0, 0, 0]
7  "If you disagree with imperialism, youre a sup...  [0, 0, 0, 0, 0, 0]
8  "italian" as a national identity is totally ov...  [0, 0, 0, 0, 0, 0]
9    "No to ethnic cleansing". QudsDay QudsMainIssue  [0, 0, 0, 0, 0, 0]

In [37]:
test.head(10)

text  \
0                   God is with Ukraine and Zelensky   
1  4 Dems, 2 Republicans Luzerne County Council s...   
2  Abuse Survivor Recounts Her Struggles at YWCA ...   
3    After Rwanda, another deportation camp disaster   
4  Another plea in Trump election interference probe   
5              any number of southern red states tbh   
6     Breitbart is the new age grocery aisle tabloid   
7     Congressman talks border security, debit limit   
8  Cooke Co. GOP incumbents announce reelection runs   
9                 Could one overwhelm the iron dome?   

                                 labels  
0  [None, None, None, None, None, None]  
1  [None, None, None, None, None, None]  
2  [None, None, None, None, None, None]  
3  [None, None, None, None, None, None]  
4  [None, None, None, None, None, None]  
5  [None, None, None, None, None, None]  
6  [None, None, None, None, None, None]  
7  [None, None, None, None, None, None]  
8  [None, None, None, None, None, None]  
9  [None, None, None, None, None, None]

In [38]:
test_final.head(10)

text  \
0  OP! Podcast where you ascertain the immigratio...   
1  "...the latest sign that Israel is planning fo...   
2  "Ice discs, ice circles, ice pans, ice pancake...   
3  "Since 2021, USAIDWest Bank and Gaza has inves...   
4  "The Cybersecurity Infrastructure Security Age...   
5  "What is lacking about your identity?" Nothing...   
6  1 x.comImamofpeace... Four key facts Hezbollah...   
7   11 more hostages freed in Gaza IsraelHamas truce   
8  2024 Republican race is a referendum on Joe Bi...   
9            2026 impeachment is coming. Maybe 2025.   

                                 labels  
0  [None, None, None, None, None, None]  
1  [None, None, None, None, None, None]  
2  [None, None, None, None, None, None]  
3  [None, None, None, None, None, None]  
4  [None, None, None, None, None, None]  
5  [None, None, None, None, None, None]  
6  [None, None, None, None, None, None]  
7  [None, None, None, None, None, None]  
8  [None, None, None, None, None, None]  
9  [None, None, None, None, None, None]

In [39]:
test = test_final
test.head(10)

text  \
0  OP! Podcast where you ascertain the immigratio...   
1  "...the latest sign that Israel is planning fo...   
2  "Ice discs, ice circles, ice pans, ice pancake...   
3  "Since 2021, USAIDWest Bank and Gaza has inves...   
4  "The Cybersecurity Infrastructure Security Age...   
5  "What is lacking about your identity?" Nothing...   
6  1 x.comImamofpeace... Four key facts Hezbollah...   
7   11 more hostages freed in Gaza IsraelHamas truce   
8  2024 Republican race is a referendum on Joe Bi...   
9            2026 impeachment is coming. Maybe 2025.   

                                 labels  
0  [None, None, None, None, None, None]  
1  [None, None, None, None, None, None]  
2  [None, None, None, None, None, None]  
3  [None, None, None, None, None, None]  
4  [None, None, None, None, None, None]  
5  [None, None, None, None, None, None]  
6  [None, None, None, None, None, None]  
7  [None, None, None, None, None, None]  
8  [None, None, None, None, None, None]  
9  [None, None, None, None, None, None]

In [40]:
from datetime import datetime, timedelta
import os
PATH = "./outputs/{}/".format((datetime.now() + timedelta(hours=2)).strftime("%d-%m-%Y-%H-%M"))
print("Current working dir:", PATH)
os.mkdir(PATH)

Current working dir: ./outputs/31-01-2026-18-24/


In [41]:
models = {
    "mbert-cased": {
        "model_type": "bert",
        "model_name": "models--google-bert--bert-base-multilingual-cased"
    },
    "mbert-uncased": {
        "model_type": "bert",
        "model_name": "models--google-bert--bert-base-multilingual-uncased"
    },
    "roberta": {
        "model_type": "roberta",
        "model_name": "models--FacebookAI--roberta-base"
    },
    "beto-cased": {
        "model_type": "bert",
        "model_name": "models--dccuchile--bert-base-spanish-wwm-cased"
    },
    "beto-uncased": {
        "model_type": "bert",
        "model_name": "models--dccuchile--bert-base-spanish-wwm-uncased"
    },
    "distilbert-multi": {
        "model_type": "distilbert",
        "model_name": "models--distilbert--distilbert-base-multilingual-cased"
    }
}

In [42]:
from simpletransformers.classification import MultiLabelClassificationModel, MultiLabelClassificationArgs
for model, fields in models.items():
  model_args = MultiLabelClassificationArgs(
      overwrite_output_dir= True,
      eval_batch_size=8,
      num_train_epochs=5,
      learning_rate = 4e-05,
      optimizer="AdamW",
      manual_seed=SEED,
      use_early_stopping=True,
      save_model_every_epoch=False
  )
  model_args.output_dir = os.path.join(PATH, model)
  models[model] = MultiLabelClassificationModel(fields["model_type"], fields["model_name"],
                                      args=model_args, num_labels=len(labels), use_cuda=use_cuda)

Some weights of BertForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--google-bert--bert-base-multilingual-cased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of BertForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--google-bert--bert-base-multilingual-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of RobertaForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--FacebookAI--roberta-base and are newly initialized: ['classifier.out_proj.weight', 'classifier.dense.weight', 'roberta.pooler.dense.bias', 'roberta.pooler.dense.weight', 'classifier.dense.bias', 'classifier.out_

In [43]:
from sklearn.metrics import mean_squared_error
from math import sqrt
def root_mean_squared_error(y_true, y_pred):    
  return sqrt(mean_squared_error(y_true, y_pred))

In [ ]:
for model_name, model in models.items():
  model.train_model(train, loss_fct=root_mean_squared_error)

6it [00:04,  1.40it/s]                                                                                                                                                                                                                  
Epoch 5 of 5: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 5/5 [02:02<00:00, 24.41s/it]
6it [00:05,  1.10it/s]                                                                                                                                                                                                                  
Epoch 5 of 5: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 5/5 [01:36<00:00, 19.25s/it]
6it [00:05,  1.16it/s]                                              

In [ ]:
import collections
from itertools import combinations
models_names = list(models.keys())
ensembles_list = list()
for i in range(1, len(models_names) + 1):
    ensembles_list += list(combinations(models_names, i))
ensembles_list = [list(ensemble) for ensemble in ensembles_list]
ensembles = {}
for i in range(len(ensembles_list)):
  ensembles["ensemble{:02d}".format(i)] = {}
  ensembles["ensemble{:02d}".format(i)]["models"] = ensembles_list[i]
  ensembles["ensemble{:02d}".format(i)]["metrics"] = {}
ensembles

In [46]:
from sklearn.metrics import accuracy_score, precision_recall_fscore_support, f1_score
def compute_metrics(y_true, y_pred):
  macro_precision, macro_recall, macro_f1, _ = precision_recall_fscore_support(y_true, y_pred, average='macro')
  acc = accuracy_score(y_true, y_pred)
  weighted_f1 = f1_score(y_true, y_pred, average='weighted')
  return {
      'accuracy': round(acc, 5),
      'macro_f1': round(macro_f1, 5),
      'macro_precision': round(macro_precision, 5),
      'macro_recall': round(macro_recall, 5),
      'weighted_f1': round(weighted_f1, 5)
  }
model_evaluation = {}
for model_name in models:
  model_evaluation[model_name] = {}
  result, model_outputs, wrong_predictions = models[model_name].eval_model(val, metric=root_mean_squared_error)
  model_evaluation[model_name]["result"] = result                                                                   
  model_evaluation[model_name]["val_model_outputs"] = model_outputs                                                 
  model_evaluation[model_name]["val_predictions"] = list ()
  for output in model_outputs:
    model_evaluation[model_name]["val_predictions"].append([0 if lab_output < 0.5 else 1 for lab_output in output]) 
  model_evaluation[model_name]["val_wrong_predictions"] = wrong_predictions                                         
  model_evaluation[model_name]["metrics"] = compute_metrics(val.get("labels").tolist(), model_evaluation[model_name].get("val_predictions"))
  print(f"{model_name}\t", model_evaluation[model_name].get("metrics"))

6it [00:05,  1.20it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 335/335 [00:05<00:00, 62.08it/s]


beto-cased	 {'accuracy': 0.6861, 'macro_f1': 0.73743, 'macro_precision': 0.7218, 'macro_recall': 0.76175, 'weighted_f1': 0.76394}


6it [00:04,  1.24it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 335/335 [00:04<00:00, 71.23it/s]


beto-uncased	 {'accuracy': 0.6775, 'macro_f1': 0.71638, 'macro_precision': 0.71496, 'macro_recall': 0.72691, 'weighted_f1': 0.7472}


6it [00:04,  1.22it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 335/335 [00:02<00:00, 116.49it/s]


distilbert-multi	 {'accuracy': 0.71338, 'macro_f1': 0.76419, 'macro_precision': 0.77634, 'macro_recall': 0.76061, 'weighted_f1': 0.7864}


In [47]:
from sklearn.preprocessing import normalize
def vote(predictions, weighted=False, weights=None):
  votes = list()  
  for i in range(len(labels)):    
    curr_label_preds = [preds[i] for preds in predictions]    
    voting = sum(curr_label_preds * weights) if weighted else sum(curr_label_preds)/len(curr_label_preds)
    votes.append(0 if voting < 0.5 else 1)  
  return votes
ensemble_evaluation = {}
def predict_ensemble(ensemble_name, dataset_name, dataset, weighted=False):
  ensemble_evaluation[ensemble_name][f"{dataset_name}_predictions"] = list()  
  for i in range(len(dataset.index)):
    predictions = list()
    ensemble_models = ensembles[ensemble_name].get("models")      
    for model_name in ensemble_models:
      curr_model_outputs = model_evaluation[model_name].get(f"{dataset_name}_model_outputs")
      predictions.append(curr_model_outputs[i])
    weights = list()    
    if weighted:      
      f1_scores_list = [model_evaluation[model_name]["metrics"].get("weighted_f1")                        
                        for model_name in ensembles[ensemble_name].get("models")]
      weights = normalize([f1_scores_list], norm="l1")[0]
    ensemble_pred = vote(predictions, weighted, weights)
    ensemble_evaluation[ensemble_name][f"{dataset_name}_predictions"].append(ensemble_pred)
for ensemble_name in ensembles:
  ensemble_evaluation[ensemble_name] = {}
  ensemble_evaluation[ensemble_name]["val_predictions"] = list()
  predict_ensemble(ensemble_name, "val", val, weighted=WEIGHTED)
  ensembles[ensemble_name]["metrics"] = compute_metrics(val.get("labels").tolist(), ensemble_evaluation[ensemble_name].get("val_predictions"))  
  print(f"{ensemble_name}\t", ensembles[ensemble_name].get("metrics"))

ensemble00	 {'accuracy': 0.69021, 'macro_f1': 0.71216, 'macro_precision': 0.7351, 'macro_recall': 0.71267, 'weighted_f1': 0.74921}
ensemble01	 {'accuracy': 0.69432, 'macro_f1': 0.74711, 'macro_precision': 0.75184, 'macro_recall': 0.75178, 'weighted_f1': 0.77145}
ensemble02	 {'accuracy': 0.66928, 'macro_f1': 0.66934, 'macro_precision': 0.73309, 'macro_recall': 0.65757, 'weighted_f1': 0.71043}
ensemble03	 {'accuracy': 0.6861, 'macro_f1': 0.73743, 'macro_precision': 0.7218, 'macro_recall': 0.76175, 'weighted_f1': 0.76394}
ensemble04	 {'accuracy': 0.6775, 'macro_f1': 0.71638, 'macro_precision': 0.71496, 'macro_recall': 0.72691, 'weighted_f1': 0.7472}
ensemble05	 {'accuracy': 0.71338, 'macro_f1': 0.76419, 'macro_precision': 0.77634, 'macro_recall': 0.76061, 'weighted_f1': 0.7864}
ensemble06	 {'accuracy': 0.70291, 'macro_f1': 0.75007, 'macro_precision': 0.77555, 'macro_recall': 0.743, 'weighted_f1': 0.77843}
ensemble07	 {'accuracy': 0.68834, 'macro_f1': 0.69881, 'macro_precision': 0.75972, '

In [48]:
import json
with open(os.path.join(PATH, 'ensembles.json'), 'w', encoding='utf-8') as f:
    json.dump(ensembles, f, ensure_ascii=False, indent=4)

In [49]:
f1_scores = {ensemble_name: ensembles[ensemble_name]["metrics"].get("weighted_f1") for ensemble_name in ensemble_evaluation}
best_ensemble_name = max(f1_scores, key=f1_scores.get)
best_ensemble = {"name": best_ensemble_name,                 
                "models": ensembles[best_ensemble_name].get("models"),                 
                "metrics": ensembles[best_ensemble_name].get("metrics")                 
                }
best_ensemble

{'name': 'ensemble35',
 'models': ['mbert-uncased', 'beto-cased', 'distilbert-multi'],
 'metrics': {'accuracy': 0.71487,
  'macro_f1': 0.77314,
  'macro_precision': 0.79133,
  'macro_recall': 0.76796,
  'weighted_f1': 0.79643}}

In [50]:
for model_name in models:
  model_predictions, model_raw_outputs = models.get(model_name).predict(test["text"].tolist())
  model_evaluation[model_name]["test_model_outputs"] = model_raw_outputs
  model_evaluation[model_name]["test_predictions"] = list ()  
  for output in model_raw_outputs:
    model_evaluation[model_name]["test_predictions"].append([0 if lab_output < 0.5 else 1 for lab_output in output])
predict_ensemble(best_ensemble.get("name"), "test", test, weighted=WEIGHTED)

3it [00:03,  1.30s/it]                                                                                                                                                                                                                  
100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 182/182 [00:02<00:00, 74.01it/s]
3it [00:03,  1.09s/it]                                                                                                                                                                                                                  
100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 182/182 [00:02<00:00, 74.07it/s]
3it [00:03,  1.22s/it]                                              

In [51]:
for model_name, evaluation in model_evaluation.items():
  curr_model = model_evaluation.get(model_name)
  curr_model["val_model_outputs"] = [list(output) for output in curr_model.get("val_model_outputs")]
  curr_model["test_model_outputs"] = [list(output) for output in curr_model.get("test_model_outputs")]
  curr_model["val_predictions"] = list(curr_model.get("val_predictions"))
  curr_model["test_predictions"] = list(curr_model.get("test_predictions"))
  if curr_model.get("val_wrong_predictions"):
    curr_model["val_wrong_predictions_list"] = curr_model.get("val_wrong_predictions")
    curr_model["val_wrong_predictions"] = {}
    for pred in curr_model.get("val_wrong_predictions_list"):
      curr_model["val_wrong_predictions"][pred.guid] = {
          "text_a": pred.text_a,
          "text_b": pred.text_b,
          "label": pred.label
      }
    del curr_model["val_wrong_predictions_list"]

  with open(os.path.join(PATH, f'{model_name}/model-evaluation.json'), 'w', encoding='utf-8') as f:
    json.dump(curr_model, f, ensure_ascii=False, indent=4)

In [52]:
best_ensemble["val_predictions"] = ensemble_evaluation[best_ensemble.get("name")].get("val_predictions")
best_ensemble["test_predictions"] = ensemble_evaluation[best_ensemble.get("name")].get("test_predictions")
with open(os.path.join(PATH, 'best-ensemble.json'), 'w', encoding='utf-8') as f:
    json.dump(best_ensemble, f, ensure_ascii=False, indent=4)

In [53]:
test["predicted_labels"] = ensemble_evaluation[best_ensemble.get("name")].get("test_predictions")
test.head(10)

text  \
0  OP! Podcast where you ascertain the immigratio...   
1  "...the latest sign that Israel is planning fo...   
2  "Ice discs, ice circles, ice pans, ice pancake...   
3  "Since 2021, USAIDWest Bank and Gaza has inves...   
4  "The Cybersecurity Infrastructure Security Age...   
5  "What is lacking about your identity?" Nothing...   
6  1 x.comImamofpeace... Four key facts Hezbollah...   
7   11 more hostages freed in Gaza IsraelHamas truce   
8  2024 Republican race is a referendum on Joe Bi...   
9            2026 impeachment is coming. Maybe 2025.   

                                 labels    predicted_labels  
0  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
1  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
2  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
3  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
4  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
5  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
6  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
7  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
8  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
9  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]

In [54]:
test.to_csv(os.path.join(PATH, "test-predictions.csv"), index=False)  